## Land Cover Classification in the Deschutes River – Capitol Lake Subwatershed, WA

### Introduction
### Study Area
### Methods
### Data Citation

In this notebook, you will use a k-means **unsupervised** clustering
algorithm to group pixels by similar spectral signatures. **k-means** is
an **exploratory** method for finding patterns in data. Because it is
unsupervised, you don’t need any training data for the model. You also
can’t measure how well it “performs” because the clusters will not
correspond to any particular land cover class. However, we expect at
least some of the clusters to be identifiable as different types of land
cover.

You will use the [harmonized Sentinel/Landsat multispectral
dataset](https://lpdaac.usgs.gov/documents/1698/HLS_User_Guide_V2.pdf).
You can access the data with an [Earthdata
account](https://www.earthdata.nasa.gov/learn/get-started) and the
[`earthaccess` library from
NSIDC](https://github.com/nsidc/earthaccess):

## STEP 1: Set up

### Step 1a: Load libraries and set GDAL parameters

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Import all libraries you will need for this analysis</li>
<li>Configure GDAL parameters to help avoid connection errors:
<code>python      os.environ["GDAL_HTTP_MAX_RETRY"] = "5"      os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"</code></li>
</ol></div></div>

In [1]:
### Import libraries
# Create reproducible file paths
import os

# Serializing and unserializing objects (save objects to disk and load later)
import pickle

# Regular expressions
import re

# Give warnings
import warnings

# Project coordinate systems for spatial data and mapping
import cartopy.crs as ccrs

# Access satellite imagery through the NASA API
import earthaccess

# Spatial data analysis
import earthpy as et

# Work with vector/shapefiles
import geopandas as gpd

# Vizualization tools
import geoviews as gv
import hvplot.pandas
import hvplot.xarray

# Work with arrays
import numpy as np

# Work with tabular data
import pandas as pd

# Work with raster data
import rioxarray as rxr
import rioxarray.merge as rxrmerge
import xarray as xr

# Use progress bar
from tqdm.notebook import tqdm
from ipywidgets import IntProgress
from IPython.display import display

# Polygons
from shapely.geometry import Polygon

# Use kmeans clustering
from sklearn.cluster import KMeans

### set GDAL (Geospatial Data Abstraction Library) parameters
os.environ["GDAL_HTTP_MAX_RETRY"] = "5"
os.environ["GDAL_HTTP_RETRY_DELAY"] = "1"

### don't show non-critical warnings
warnings.simplefilter('ignore')

c:\Users\nymve\miniconda3\envs\earth-analytics-python\Lib\site-packages\earthpy\__init__.py:7: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  from pkg_resources import resource_string


### Step 1b: Run the caching decorator

Below you can find code for a caching **decorator** which you can use in
your code. To use the decorator:

``` python
@cached(key, override)
def do_something(*args, **kwargs):
    ...
    return item_to_cache
```

This decorator will **pickle** the results of running the
`do_something()` function, and only run the code if the results don’t
already exist. To override the caching, for example temporarily after
making changes to your code, set `override=True`. Note that to use the
caching decorator, you must write your own function to perform each
task!

You might notice that typically in these assignments, we start by creating a data_dir to store our data files. Here, our caching decorator is making the data directory for us.

In [ ]:
### make the caching decorator
def cached(func_key, override=False): # Add =True if wanting to rerun
    """
    A decorator to cache function results
    
    Parameters
    ==========
    key: str
      File basename used to save pickled results
    override: bool
      When True, re-compute even if the results are already stored
    """
    def compute_and_cache_decorator(compute_function):
        """
        Wrap the caching function
        
        Parameters
        ==========
        compute_function: function
          The function to run and cache results
        """
        def compute_and_cache(*args, **kwargs):
            """
            Perform a computation and cache, or load cached result.
            
            Parameters
            ==========
            args
              Positional arguments for the compute function
            kwargs
              Keyword arguments for the compute function
            """
            ### Add an identifier from the particular function call
            if 'cache_key' in kwargs:
                key = '_'.join((func_key, kwargs['cache_key']))
            else:
                key = func_key

            ### define a file path based on the directory structure in earthpy
            path = os.path.join(
                
                ### earthpy directory
                et.io.HOME, 
                
                ### earthpy dataset
                et.io.DATA_NAME, 
                
                ### make a subdirectory called "jars"
                'jars', 
                
                ### use f-string (formatted string) to create a string by embedding the value
                ### of the variable "key" into the string 
                ### use .pickle file extension (a pickle file is a serialized python objecT)
                f'{key}.pickle')
            
            ### Check if the cache exists already or if we should override caching
            if not os.path.exists(path) or override:
                
                ### Make jars directory if needed
                os.makedirs(os.path.dirname(path), exist_ok=True)
                
                ### Run the compute function as the user did
                result = compute_function(*args, **kwargs)
                
                ### Pickle the object (save to file)
                ### open the file at filename (wb - write binary)
                with open(path, 'wb') as file:
                    
                    ### save the result without needing to recompute when loading
                    ### it back into Python
                    pickle.dump(result, file)
            
            ### if the file already exists/we are not overriding the cache
            else:
               
                ### Unpickle the object (load the cached result) (rb - read binary)
                with open(path, 'rb') as file:
                    
                    ### use pickle.load to unserialize the file back into a python object
                    result = pickle.load(file)
                    
            return result
        
        return compute_and_cache
    
    return compute_and_cache_decorator

## STEP 2: Study site

For this analysis, you will use a watershed from the [Water Boundary
Dataset](https://www.usgs.gov/national-hydrography/access-national-hydrography-products),
HU12 watersheds (WBDHU12.shp).

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Download the Water Boundary Dataset for region 8 (Mississippi)</li>
<li>Select watershed 080902030506</li>
<li>Generate a site map of the watershed</li>
</ol>
<p>Try to use the <strong>caching decorator</strong></p></div></div>

We chose this watershed because it covers parts of New Orleans an is
near the Mississippi Delta. Deltas are boundary areas between the land
and the ocean, and as a result tend to contain a rich variety of
different land cover and land use types.

In [23]:
# Assign the hydrologic unit code
HUC_LEVEL = 12

# Download, unzip, and read shapefile, using cache decorator
@cached(f'wbd_17_hu{HUC_LEVEL}_gdf')

# Make a function to read in the file
def read_wbd_file(wbd_filename, cache_key=None):

    # Define the URL we're pulling data from
    wbd_url = (

        ### add base URL
        "https://prd-tnm.s3.amazonaws.com/StagedProducts/Hydrography/WBD/HU12/Shape/"

        # Insert the name of the specific file we want
        f"{wbd_filename}.zip"
    )

    # Download data and unzip it into the directory
    wbd_dir = et.data.get_data(url = wbd_url)

    # Path to shapefile in the fir
    wbd_path = os.path.join(wbd_dir,
                            'Shape',                            
                            f'WBDHU{HUC_LEVEL}.shp')
    
    # Read the shp as gdf
    wbd_gdf = gpd.read_file(wbd_path,
                            
                            # Use pyogrio library
                            engine = 'pyogrio')
    
    # Give us the gdf for the watershed boundary
    return wbd_gdf

In [24]:
# open the shapefile using the read_wbd_file function that we created
wbd_gdf = read_wbd_file("WBD_17_HU2_Shape",
                        f'hu{HUC_LEVEL}')

In [25]:
# Look at data
wbd_gdf

tnmid  \
0     {0E4E6573-8B28-4F8C-B959-694DE3A9F91C}   
1     {07FD06B3-4536-4B3D-A598-8D646D308101}   
2     {8720D0B0-BEF6-492F-B878-1B0343DB67DD}   
3     {F673354E-0002-4C26-8E80-CFA9C84F31AA}   
4     {546E09D7-5785-4B5B-A284-634E682D7C41}   
...                                      ...   
8928  {2CEBB4FF-1A8E-4DA4-94EF-2B790B6C3117}   
8929  {367A4656-FF42-48AB-A264-5C8B038FE546}   
8930  {076A17A9-ACFD-4833-A00B-00B72882C5BC}   
8931  {67211EB6-B26C-4553-B6DF-B576BA652C5C}   
8932  {B609D074-6302-43A5-A9EA-49B2E7A10681}   

                                  metasource  \
0     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
1     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
2     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
3     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
4     {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
...                                      ...   
8928  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
8929  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
8930  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
8931  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   
8932  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}   

                            sourcedata  \
0     Watershed Boundary Dataset (WBD)   
1     Watershed Boundary Dataset (WBD)   
2     Watershed Boundary Dataset (WBD)   
3     Watershed Boundary Dataset (WBD)   
4     Watershed Boundary Dataset (WBD)   
...                                ...   
8928  Watershed Boundary Dataset (WBD)   
8929  Watershed Boundary Dataset (WBD)   
8930  Watershed Boundary Dataset (WBD)   
8931  Watershed Boundary Dataset (WBD)   
8932  Watershed Boundary Dataset (WBD)   

                                             sourceorig sourcefeat   loaddate  \
0     Natural Resources and Conservation Service and...       None 2024-08-15   
1     Natural Resources and Conservation Service and...       None 2024-08-15   
2     Natural Resources and Conservation Service and...       None 2024-08-15   
3     Natural Resources and Conservation Service and...       None 2024-08-15   
4     Natural Resources and Conservation Service and...       None 2024-08-15   
...                                                 ...        ...        ...   
8928  Natural Resources and Conservation Service and...       None 2024-08-15   
8929  Natural Resources and Conservation Service and...       None 2024-08-15   
8930  Natural Resources and Conservation Service and...       None 2024-08-15   
8931  Natural Resources and Conservation Service and...       None 2024-08-15   
8932  Natural Resources and Conservation Service and...       None 2024-08-15   

           referenceg  areaacres  areasqkm states  ...  \
0             1148597   12257.36     49.60     OR  ...   
1     1127639,1147060   21300.40     86.20     OR  ...   
2             1519865   17826.81     72.14     CN  ...   
3             1146937   15583.39     63.06     OR  ...   
4       384804,388149   19147.98     77.49     ID  ...   
...               ...        ...       ...    ...  ...   
8928          1162590   12778.53     51.71     OR  ...   
8929           374733   23055.80     93.30     ID  ...   
8930           377793   13336.23     53.97     ID  ...   
8931          1149920   18962.85     76.74     OR  ...   
8932  1141306,1151904   23695.41     95.89     OR  ...   

                                     name hutype     humod         tohuc  \
0                              Rock Creek      S        NM  170900050403   
1         Stout Creek-North Santiam River      M        NM  170900050602   
2                   Lower Galbraith Creek      S        NM  170101010306   
3     Headwaters North Fork Crooked River      S  DD,IT,CD  170703040308   
4         Little Deer Creek-Panther Creek      S        NM  170602031201   
...                                   ...    ...       ...           ...   
8928                        Corral Spring      C        NM  CLOSED BASIN   
8929                           Rock Lakes      S  ID,GC,CD  170402150505   
8930                      

In [26]:
### Filter the shapefile to the specific watershed we're using

# Define the gdf for the watershed by subsetting the gdf of the whole watershed dataset
deschutes_gdf = wbd_gdf[wbd_gdf[
                
    # Filter the gdf to the row(s) with the watershe we want 
    # Use "dissolve" to merge the geometries of all the rows matching the target watershed            
    f'huc{HUC_LEVEL}'].isin(['171100160202'])].dissolve() 



### check it out
deschutes_gdf

geometry  \
0  POLYGON ((-122.93753 47.06808, -122.93588 47.0...   

                                    tnmid  \
0  {694A30A3-78CE-48CA-9267-A52677CB0673}   

                               metasource                        sourcedata  \
0  {511D2AC8-11BA-45FC-AB98-F69D693D4C44}  Watershed Boundary Dataset (WBD)   

                                          sourceorig sourcefeat   loaddate  \
0  Natural Resources and Conservation Service and...       None 2024-08-15   

        referenceg  areaacres  areasqkm  ...         huc12  \
0  1518684,1513902   24427.95     98.86  ...  171100160202   

                           name hutype humod         tohuc noncontrib  \
0  Deschutes River-Capitol Lake      S    NM  171100190900        0.0   

   noncontr_1  shape_Leng  shape_Area  ObjectID  
0         0.0         NaN         NaN       163  

[1 rows x 21 columns]

In [27]:
### Make a site map with satellite imagery in the background
(
    # Project the delta_gdf to Mercator
    deschutes_gdf.to_crs(ccrs.Mercator())

    # Use hvplot
    .hvplot(

        # Make the watershed transparent
        alpha = 0.40, fill_color = "white",

        # Add satellite basemap
        tiles = 'EsriImagery',

        crs = ccrs.Mercator())

        # Set plot size
        .opts(width = 600, height = 300)
)


:Overlay
   .WMTS.I     :WMTS   [Longitude,Latitude]
   .Polygons.I :Polygons   [Longitude,Latitude]

The watershed site for this analysis is in the Mississippi Delta to the southeast outskirts of New Orleans, Louisiana. The watershed boundary was determined from the USGS National Watershed Boundary dataset at the Hydrologic Unit Code (HUC) 12 - 080902030506. This area is experiencing rapid land loss, salt water intrusion, and wetland degradation (USGS, 2011). New Orleans was originally built on a wetland habitat and is a below sea level community on a delta. It experiences unique challenges that come from coastal and deltaic hydrologic processes including flooding and sediment deposits (Day et al., 2007). The city and area is experiencing significant water-related threats due to climate change, and currently depends on levees and pumps for its survival (Day et al., 2021).

<u>Data citation:</u>
U.S. Geological Survey, 2024, National watershed boundary (HUC12) dataset for the conterminous United States, retrieved [02/06/2026], from https://data.usgs.gov/datacatalog/data/USGS:63d31e73d34e06fef1501265. 

## STEP 3: Multispectral data

### Step 3a: Search for data

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Log in to the <code>earthaccess</code> service using your Earthdata
credentials:
<code>python      earthaccess.login(persist=True)</code></li>
<li>Modify the following sample code to search for granules of the
HLSL30 product overlapping the watershed boundary from May to October
2023 (there should be 76 granules):
<code>python      results = earthaccess.search_data(          short_name="...",          cloud_hosted=True,          bounding_box=tuple(gdf.total_bounds),          temporal=("...", "..."),      )</code></li>
</ol></div></div>

In [28]:
### Log in to earthaccess
earthaccess.login(persist = True)

In [29]:
### Search for HLS granules we want
results = earthaccess.search_data(

    ### Specify which dataset and spatial resolution we want 
    short_name = "HLSL30",

    ### Specify that we're using cloud data
    cloud_hosted = True,

    ### Use the bounding box from our watershed boundary
    bounding_box = tuple(deschutes_gdf.total_bounds),

    ### set the temporal range of the data
    temporal = ("2024-06", "2024-08")
)

In [30]:
results

[Collection: {'EntryTitle': 'HLS Landsat Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0'}
 Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -122.33034656, 'Latitude': 46.86374115}, {'Longitude': -121.92318169, 'Latitude': 47.84865186}, {'Longitude': -123.00026736, 'Latitude': 47.85370184}, {'Longitude': -123.00026241, 'Latitude': 46.86569987}, {'Longitude': -122.33034656, 'Latitude': 46.86374115}]}}]}}}
 Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2024-06-06T19:00:55.253Z', 'EndingDateTime': '2024-06-06T19:00:55.253Z'}}
 Size(MB): 110.67294883728027
 Data: ['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B06.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B10.tif', 'https://d

### Step 3b: Compile information about each granule

I recommend building a GeoDataFrame, as this will allow you to plot the
granules you are downloading and make sure they line up with your
shapefile. You could also use a DataFrame, dictionary, or a custom
object to store this information.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each search result:
<ol type="1">
<li>Get the following information (HINT: look at the [‘umm’] values for
each search result):
<ul>
<li>granule id (UR)</li>
<li>datetime</li>
<li>geometry (HINT: check out the shapely.geometry.Polygon class to
convert points to a Polygon)</li>
</ul></li>
<li>Open the granule files. I recommend opening one granule at a time,
e.g. with (<code>earthaccess.open([result]</code>).</li>
<li>For each file (band), get the following information:
<ul>
<li>file handler returned from <code>earthaccess.open()</code></li>
<li>tile id</li>
<li>band number</li>
</ul></li>
</ol></li>
<li>Compile all the information you collected into a GeoDataFrame</li>
</ol></div></div>

In [31]:
### Make a function to process all the granules from the earthaccess search
### And extract information for each granule

# Define the function
def get_earthaccess_links(results):

    # Make and display a progress bar
    f = IntProgress(min = 0, max = len(results), description = 'Open granules')
    display(f)

    # Use a regular expression to extract tile_id and bank from .tif files
    url_re = re.compile(
        r'\.(?P<tile_id>\w+)\.\d+T\d+\.v\d\.\d\.(?P<band>[A-Za-z0-9]+)\.tif')

    # Accumulate gdf rows from each granule
    link_rows = []

    # Loop over granules to extract info
    for granule in results:

        # Locate metadata (UMM = universal metadata model)
        info_dict = granule['umm']

        # Pull out unique identifier for the granule
        granule_id = info_dict['GranuleUR']

        # Extract date/time 
        datetime = pd.to_datetime(
            info_dict['TemporalExtent']['RangeDateTime']['BeginningDateTime']
        )

        # Extact boundary coordinates for granule
        points = (
            info_dict
            ['SpatialExtent']['HorizontalSpatialDomain']['Geometry']['GPolygons'][0]
            ['Boundary']['Points']
        )

        # Make polygon using coordinate points for granule
        geometry = Polygon(
            [(point['Longitude'],
              point['Latitude']) for point in points]
        )

        # Get url and open granule
        files = earthaccess.open([granule])

        # Loop through each file in the granule
        for file in files:

            # Use url regular expression to get url
            match = url_re.search(file.full_name)

            # If match is found, append data to link_rows gdf we initialized
            if match is not None: 
                link_rows.append(

                    # Makes a gdf with the granule's data and geometry
                    gpd.GeoDataFrame(
                        dict(

                        # Timestamp
                        datetime = [datetime],

                        # Unique ID
                        tile_id = [match.group('tile_id')],

                        # Spectral band name
                        band = [match.group('band')],

                        # url
                        url = [file],

                        geometry = [geometry]
                    ),

                    # Set crs
                    crs ="EPSG:4326"
                )
            )

        # Update progress bar after each granule is done
        f.value += 1

    # Combine into a single gdf   
    file_df = pd.concat(link_rows).reset_index(drop = True)

    # Return the final gdf file
    return file_df

In [32]:
granule = results[0]

granule

Collection: {'EntryTitle': 'HLS Landsat Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0'}
Spatial coverage: {'HorizontalSpatialDomain': {'Geometry': {'GPolygons': [{'Boundary': {'Points': [{'Longitude': -122.33034656, 'Latitude': 46.86374115}, {'Longitude': -121.92318169, 'Latitude': 47.84865186}, {'Longitude': -123.00026736, 'Latitude': 47.85370184}, {'Longitude': -123.00026241, 'Latitude': 46.86569987}, {'Longitude': -122.33034656, 'Latitude': 46.86374115}]}}]}}}
Temporal coverage: {'RangeDateTime': {'BeginningDateTime': '2024-06-06T19:00:55.253Z', 'EndingDateTime': '2024-06-06T19:00:55.253Z'}}
Size(MB): 110.67294883728027
Data: ['https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B06.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B10.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B01.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.VZA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.VAA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B03.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B07.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B04.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.Fmask.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B05.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B09.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.SZA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B02.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.SAA.tif', 'https://data.lpdaac.earthdatacloud.nasa.gov/lp-prod-protected/HLSL30.020/HLS.L30.T10TET.2024158T190055.v2.0/HLS.L30.T10TET.2024158T190055.v2.0.B11.tif']

In [33]:
info_dict = granule['umm']
info_dict

{'TemporalExtent': {'RangeDateTime': {'BeginningDateTime': '2024-06-06T19:00:55.253Z',
   'EndingDateTime': '2024-06-06T19:00:55.253Z'}},
 'GranuleUR': 'HLS.L30.T10TET.2024158T190055.v2.0',
 'AdditionalAttributes': [{'Name': 'LANDSAT_PRODUCT_ID',
   'Values': ['LC08_L1TP_047027_20240606_20240606_02_RT']},
  {'Name': 'CLOUD_COVERAGE', 'Values': ['6']},
  {'Name': 'MGRS_TILE_ID', 'Values': ['10TET']},
  {'Name': 'SPATIAL_COVERAGE', 'Values': ['60']},
  {'Name': 'SPATIAL_RESOLUTION', 'Values': ['30.0']},
  {'Name': 'SPATIAL_RESAMPLING_ALG', 'Values': ['Cubic Convolution']},
  {'Name': 'HLS_PROCESSING_TIME', 'Values': ['2024-06-25T18:12:32Z']},
  {'Name': 'SENSING_TIME', 'Values': ['2024-06-06T19:00:55.2536540Z']},
  {'Name': 'HORIZONTAL_CS_NAME', 'Values': ['UTM, WGS84, UTM ZONE 10']},
  {'Name': 'ULX', 'Values': ['499980.0']},
  {'Name': 'ULY', 'Values': ['5300040.0']},
  {'Name': 'ADD_OFFSET', 'Values': ['0']},
  {'Name': 'REF_SCALE_FACTOR', 'Values': ['0.0001']},
  {'Name': 'THERM_SCAL

In [34]:
### Run the function to get granule search results
file_df = get_earthaccess_links(results)

IntProgress(value=0, description='Open granules', max=88)

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

...

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

In [35]:
# Check to make sure its a geodataframe
type(file_df)

geopandas.geodataframe.GeoDataFrame

### Step 3c: Open, crop, and mask data

This will be the most resource-intensive step. I recommend caching your
results using the `cached` decorator or by writing your own caching
code. I also recommend testing this step with one or two dates before
running the full computation.

This code should include at least one **function** including a
numpy-style docstring. A good place to start would be a function for
opening a single masked raster, applying the appropriate scale
parameter, and cropping.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>For each granule:
<ol type="1">
<li><p>Open the Fmask band, crop, and compute a quality mask for the
granule. You can use the following code as a starting point, making sure
that <code>mask_bits</code> contains the quality bits you want to
consider: ```python # Expand into a new dimension of binary bits bits =
( np.unpackbits(da.astype(np.uint8), bitorder=‘little’)
.reshape(da.shape + (-1,)) )</p>
<p># Select the required bits and check if any are flagged mask =
np.prod(bits[…, mask_bits]==0, axis=-1) ```</p></li>
<li><p>For each band that starts with ‘B’:</p>
<ol type="1">
<li>Open the band, crop, and apply the scale factor</li>
<li>Name the DataArray after the band using the <code>.name</code>
attribute</li>
<li>Apply the cloud mask using the <code>.where()</code> method</li>
<li>Store the DataArray in your data structure (e.g. adding a
GeoDataFrame column with the DataArray in it. Note that you will need to
remove the rows for unused bands)</li>
</ol></li>
</ol></li>
</ol></div></div>

In [37]:
### Apply cached decorator to function
@cached('deschutes_reflectance_da_df')

# Write function that computes reflectance data using 
# Search results (df of urls) and watershed boundary
def compute_reflectance_da(search_results, boundary_gdf):

    """Connect to files using VSI, crop them, apply a cloud mask, and wrangle

    Return a single reflectance Dataframe with bands as columns
    and centroid coordinates and dattime as the index
    
    Parameters
    ==========
    search_results:list
        Search result links to the files (urls)
    boundary_gdf: gpd.GeoDataFrame
        Boundary used to crop the data
    """

    # Write a function to open raster from url, apply scale factor, and crop and mask data
    def open_dataarray(url, boundary_proj_gdf, scale = 1, masked = True):

        # Open raster data
        da = rxr.open_rasterio(url, masked = masked).squeeze() * scale  

        # Reproject the boundary needed to match the raster crs
        if boundary_proj_gdf is None:
            boundary_proj_gdf = boundary_gdf.to_crs(da.rio.crs)

        # Crop the raster to the bounding box
        cropped = da.rio.clip_box(*boundary_proj_gdf.total_bounds)

        # Return the cropped image of that tile
        return cropped

    # Write function to apply a cloud mask
    def compute_quality_mask(da, mask_bits = [1, 2, 3]):
        
        """Mask out low quality data by bit"""
        
        # Unpack the bits to a new axis  
        bits = (

            # Unpack each number into individual bits
            np.unpackbits(

                # Convert to 8-bit unsigned integrer format
                da.astype(np.uint8),

                # Set the order of the bits
                bitorder = "little"
            # Reshampe to match original data with an extra dimension for the bits
            ).reshape(da.shape +(-1, ))
        )
        
        # Grab bits we want and check if their flagged
        mask = np.prod(

            # Open bits
            bits[
                ...,
                            mask_bits] == 0,
                            axis = -1)


        # Return the mask
        return mask
    
    # Grab metadata
    file_df = get_earthaccess_links(search_results)

    # Store results for each granule
    granule_da_rows = []

    # Store projected boundary
    boundary_proj_gdf = None

    # Group the data by each granule
    group_iter = file_df.groupby(

        # Datetime and tile_id
        ['datetime', 'tile_id'])
    
    # loop through each image and its metadata
    for (datetime, tile_id), granule_df in tqdm(group_iter):

        # Print status bar
        print(f'Processing granule {tile_id} {datetime}')

        # Find each granule's cloud mask file (fmask) url
        cloud_mask_url = (
            granule_df.loc[granule_df.band == 'Fmask', 'url']
            .values[0])
        
        # Open granule cloud cover
        cloud_masked_cropped_da = open_dataarray(cloud_mask_url, boundary_proj_gdf, scale = 1, masked = False)

        # Compute the cloud mask
        cloud_mask = compute_quality_mask(cloud_masked_cropped_da)
        
        # Loop through each spectral band to open, crop, and mask the band
        da_list = []
        df_list = []
        
        # Lop through each band in the granule
        for i, row in granule_df.iterrows():

            # Only loop through the spectral bands
            if row.band.startswith('B'):

                # Open band's raster and scale to reflectance
                band_cropped = open_dataarray(
                    row.url, boundary_proj_gdf, scale = 0.0001)
                
                # Name the raster by the band
                band_cropped.name = row.band

                # Apply the cloud mask to the raster
                row['da'] = band_cropped.where(cloud_mask)

                # Append the row to the granule_da_rows
                granule_da_rows.append(row.to_frame().T)


    # Reassemble the metadata df
    return pd.concat(granule_da_rows)

In [38]:
### apply the function
reflectance_da_df = compute_reflectance_da(results, deschutes_gdf)

IntProgress(value=0, description='Open granules', max=88)

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

...

QUEUEING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/15 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/15 [00:00<?, ?it/s]

  0%|          | 0/88 [00:00<?, ?it/s]

Processing granule T10TDS 2024-06-06 19:00:55.253000+00:00
Processing granule T10TDT 2024-06-06 19:00:55.253000+00:00
Processing granule T10TES 2024-06-06 19:00:55.253000+00:00
Processing granule T10TET 2024-06-06 19:00:55.253000+00:00
Processing granule T10TDS 2024-06-07 18:54:59.965000+00:00
Processing granule T10TDT 2024-06-07 18:54:59.965000+00:00
Processing granule T10TES 2024-06-07 18:54:59.965000+00:00
Processing granule T10TET 2024-06-07 18:54:59.965000+00:00
Processing granule T10TDS 2024-06-14 19:01:04.165000+00:00
Processing granule T10TDT 2024-06-14 19:01:04.165000+00:00
Processing granule T10TES 2024-06-14 19:01:04.165000+00:00
Processing granule T10TET 2024-06-14 19:01:04.165000+00:00
Processing granule T10TDS 2024-06-15 18:54:47.122000+00:00
Processing granule T10TDT 2024-06-15 18:54:47.122000+00:00
Processing granule T10TES 2024-06-15 18:54:47.122000+00:00
Processing granule T10TET 2024-06-15 18:54:47.122000+00:00
Processing granule T10TDS 2024-06-22 19:01:04.462000+00:

In [39]:
# Check out the dataframe
reflectance_da_df

datetime tile_id band  \
47    2024-06-06 19:00:55.253000+00:00  T10TDS  B10   
48    2024-06-06 19:00:55.253000+00:00  T10TDS  B05   
49    2024-06-06 19:00:55.253000+00:00  T10TDS  B09   
50    2024-06-06 19:00:55.253000+00:00  T10TDS  B01   
51    2024-06-06 19:00:55.253000+00:00  T10TDS  B02   
...                                ...     ...  ...   
1315  2024-08-26 18:55:25.731000+00:00  T10TET  B06   
1316  2024-08-26 18:55:25.731000+00:00  T10TET  B01   
1317  2024-08-26 18:55:25.731000+00:00  T10TET  B11   
1318  2024-08-26 18:55:25.731000+00:00  T10TET  B05   
1319  2024-08-26 18:55:25.731000+00:00  T10TET  B04   

                                                    url  \
47    <File-like object HTTPFileSystem, https://data...   
48    <File-like object HTTPFileSystem, https://data...   
49    <File-like object HTTPFileSystem, https://data...   
50    <File-like object HTTPFileSystem, https://data...   
51    <File-like object HTTPFileSystem, https://data...   
...                                                 ...   
1315  <File-like object HTTPFileSystem, https://data...   
1316  <File-like object HTTPFileSystem, https://data...   
1317  <File-like object HTTPFileSystem, https://data...   
1318  <File-like object HTTPFileSystem, https://data...   
1319  <File-like object HTTPFileSystem, https://data...   

                                               geometry  \
47    POLYGON ((-124.29100013 45.95825869, -122.8740...   
48    POLYGON ((-124.29100013 45.95825869, -122.8740...   
49    POLYGON ((-124.29100013 45.95825869, -122.8740...   
50    POLYGON ((-124.29100013 45.95825869, -122.8740...   
51    POLYGON ((-124.29100013 45.95825869, -122.8740...   
...                                                 ...   
1315  POLYGON ((-121.55985018 46.85663988, -121.5327...   
1316  POLYGON ((-121.55985018 46.85663988, -121.5327...   
1317  POLYGON ((-121.55985018 46.85663988, -121.5327...   
1318  POLYGON ((-121.55985018 46.85663988, -121.5327...   
1319  POLYGON ((-121.55985018 46.85663988, -121.5327...   

                                                     da  
47    [[<xarray.DataArray 'B10' ()> Size: 4B\narray(...  
48    [[<xarray.DataArray 'B05' ()> Size: 4B\narray(...  
49    [[<xarray.DataArray 'B09' ()> Size: 4B\narray(...  
50    [[<xarray.DataArray 'B01' ()> Size: 4B\narray(...  
51    [[<xarray.DataArray 'B02' ()> Size: 4B\narray(...  
...                                                 ...  
1315  [[<xarray.DataArray 'B06' ()> Size: 4B\narray(...  
1316  [[<xarray.DataArray 'B01' ()> Size: 4B\narray(...  
1317  [[<xarray.DataArray 'B11' ()> Size: 4B\narray(...  
1318  [[<xarray.DataArray 'B05' ()> Size: 4B\narray(...  
1319  [[<xarray.DataArray 'B04' ()> Size: 4B\narray(...  

[880 rows x 6 columns]

### Step 3d: Merge and Composite Data

You will notice for this watershed that:   
1. The raster data for each date are spread across 4 granules  
2. Any given image is incomplete because of clouds

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">

*   1. For each band:  
    *   a. For each date:  
        *   i. Merge all 4 granules  
        *   ii. Mask any negative values created by interpolating from the nodata value of -9999 (`rioxarray`) should account for this, but doesn't appear to when merging. If you leave these values in, they will create problems later on
    *   b. Concatenate the merged DataArrays along a new date dimension  
    *   c. Take the mean in the date dimension to create a composite image that fills cloud gaps  
    *   d. Add the band as a dimensions, and give the DataArray a name  
*   2. Concatenate along the band dimension


In [40]:
### Apply cache decorator
@cached('deschutes_reflectance_da')

# Create a function to merge and composite reflectance data from multiple granules
# End result: single, composite reflectance image for each spectral band
def merge_and_composite_arrays(granule_da_df):
    
    # Initialize a list to store composites after procesing
    da_list = []

    ### loop over each spectral band
    for band, band_df in granule_da_df.groupby('band'):

        # List for storing merged data arrays (one per date)
        merged_das = []

        # Loop over date/time of image acquisition and merge granules for each date
        for dataetime, date_df in band_df.groupby('datetime'):

            # Merge granules for each date
            merged_da = rxrmerge.merge_arrays(list(date_df.da))
           
            # Mask negative values (could be no data or invalid data)
            merged_da = merged_da.where(merged_da > 0)
            
            # Append to merged_das list we initialized
            merged_das.append(merged_da)
            
        # Composite images across dates
        composite_da = xr.concat(merged_das,
                                 
                                 # Make a datetime dimension
                                 # Calculate median value across the dateimtes for the pixel
                                dim = 'datetime').median('datetime')
        
        # Assign band number to attribute of composite data array
        composite_da['band'] = int(band[1:])

        # Name the composite data array
        composite_da.name = 'reflectance'

        # Add processed and composite data array to lsit
        da_list.append(composite_da)

    # Concatenates composite data arrays for each band along band dimension
    return xr.concat(da_list, dim = 'band')

In [41]:
# Call function to get final composite reflectance data 
reflectance_da = merge_and_composite_arrays(reflectance_da_df)

In [42]:
# Check out the data array
reflectance_da

<xarray.DataArray 'reflectance' (band: 10, y: 491, x: 561)> Size: 11MB
array([[[0.0151    , 0.0165    , 0.0159    , ..., 0.0497    ,
         0.0528    , 0.0526    ],
        [0.0158    , 0.017     , 0.0168    , ..., 0.056     ,
         0.0624    , 0.0523    ],
        [0.0163    , 0.0175    , 0.0181    , ..., 0.0606    ,
         0.0597    , 0.0473    ],
        ...,
        [0.0356    , 0.0546    , 0.0319    , ..., 0.0083    ,
         0.0087    , 0.0099    ],
        [0.0263    , 0.0487    , 0.0327    , ..., 0.0096    ,
         0.0096    , 0.0097    ],
        [0.0222    , 0.0229    , 0.0201    , ..., 0.0093    ,
         0.0083    , 0.0081    ]],

       [[0.0146    , 0.0159    , 0.0158    , ..., 0.0654    ,
         0.0672    , 0.0657    ],
        [0.0148    , 0.0165    , 0.0167    , ..., 0.0696    ,
         0.0737    , 0.0618    ],
        [0.0152    , 0.0175    , 0.0181    , ..., 0.07169999,
         0.0702    , 0.057     ],
...
        [0.269     , 0.26369998, 0.252     , ..., 0.1988    ,
         0.19849999, 0.19829999],
        [0.25779998, 0.2543    , 0.2446    , ..., 0.1978    ,
         0.1973    , 0.19669999],
        [0.2438    , 0.2417    , 0.2356    , ..., 0.19669999,
         0.1962    , 0.19559999]],

       [[0.1978    , 0.19739999, 0.19749999, ..., 0.2954    ,
         0.2956    , 0.2959    ],
        [0.1964    , 0.1955    , 0.1961    , ..., 0.3074    ,
         0.3065    , 0.305     ],
        [0.1953    , 0.1938    , 0.19469999, ..., 0.30855   ,
         0.3118    , 0.3109    ],
        ...,
        [0.2434    , 0.239     , 0.23249999, ..., 0.1919    ,
         0.1918    , 0.1918    ],
        [0.23279999, 0.23099999, 0.2263    , ..., 0.19119999,
         0.1906    , 0.1901    ],
        [0.22309999, 0.2223    , 0.2191    , ..., 0.19039999,
         0.1894    , 0.18859999]]], shape=(10, 491, 561), dtype=float32)
Coordinates:
  * band         (band) int64 80B 1 2 3 4 5 6 7 9 10 11
  * y            (y) float64 4kB 5.213e+06 5.213e+06 ... 5.198e+06 5.198e+06
  * x            (x) float64 4kB 5.019e+05 5.019e+05 ... 5.187e+05 5.187e+05
    spatial_ref  int64 8B 0

## STEP 4: K-means clustering

Cluster your data by spectral signature using the k-means algorithm.

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><ol type="1">
<li>Convert your DataArray into a <strong>tidy</strong> DataFrame of
reflectance values (hint: check out the <code>.to_dataframe()</code> and
<code>.unstack()</code> methods)</li>
<li>Filter out all rows with no data (all 0s or any N/A values)</li>
<li>Fit a k-means model. You can experiment with the number of groups to
find what works best.</li>
</ol></div></div>

In [43]:
### Convert spectral DataArray to a tidy DataFrame
model_df = (reflectance_da
            
            # Flatten the array into a long dataframe
            .to_dataframe()
            
            # Select the reflectance column
            .reflectance
            
            # Make the table wide: each row will be pixel location
            # And each column is a spectral band with the reflectance value
            .unstack('band')
)

# Check dataframe
model_df

band                    1       2       3       4       5       6       7   \
y         x                                                                  
5212725.0 501915.0  0.0151  0.0146  0.0279  0.0156  0.1930  0.0681  0.0270   
          501945.0  0.0165  0.0159  0.0314  0.0162  0.2213  0.0787  0.0312   
          501975.0  0.0159  0.0158  0.0313  0.0163  0.2185  0.0803  0.0304   
          502005.0  0.0165  0.0158  0.0293  0.0158  0.2173  0.0740  0.0299   
          502035.0  0.0168  0.0157  0.0346  0.0211  0.2444  0.0989  0.0435   
...                    ...     ...     ...     ...     ...     ...     ...   
5198025.0 518595.0  0.0093  0.0123  0.0311  0.0175  0.2348  0.0838  0.0350   
          518625.0  0.0094  0.0122  0.0318  0.0184  0.2515  0.0904  0.0368   
          518655.0  0.0093  0.0114  0.0301  0.0179  0.2413  0.0878  0.0350   
          518685.0  0.0083  0.0111  0.0282  0.0162  0.2115  0.0768  0.0320   
          518715.0  0.0081  0.0104  0.0270  0.0148  0.2052  0.0730  0.0318   

band                    9       10      11  
y         x                                 
5212725.0 501915.0  0.0009  0.2104  0.1978  
          501945.0  0.0009  0.2123  0.1974  
          501975.0  0.0009  0.2147  0.1975  
          502005.0  0.0010  0.2170  0.2017  
          502035.0  0.0008  0.2184  0.2050  
...                    ...     ...     ...  
5198025.0 518595.0  0.0009  0.1969  0.1916  
          518625.0  0.0009  0.1969  0.1911  
          518655.0  0.0008  0.1967  0.1904  
          518685.0  0.0009  0.1962  0.1894  
          518715.0  0.0010  0.1956  0.1886  

[275451 rows x 10 columns]

In [44]:
# Filter out rows with no data
model_df = model_df.drop(columns = [10,11]).dropna()

# Check the dataframe without NaN
model_df

band                     1       2       3       4       5       6       7  \
y         x                                                                  
5212725.0 501915.0  0.0151  0.0146  0.0279  0.0156  0.1930  0.0681  0.0270   
          501945.0  0.0165  0.0159  0.0314  0.0162  0.2213  0.0787  0.0312   
          501975.0  0.0159  0.0158  0.0313  0.0163  0.2185  0.0803  0.0304   
          502005.0  0.0165  0.0158  0.0293  0.0158  0.2173  0.0740  0.0299   
          502035.0  0.0168  0.0157  0.0346  0.0211  0.2444  0.0989  0.0435   
...                    ...     ...     ...     ...     ...     ...     ...   
5198025.0 518595.0  0.0093  0.0123  0.0311  0.0175  0.2348  0.0838  0.0350   
          518625.0  0.0094  0.0122  0.0318  0.0184  0.2515  0.0904  0.0368   
          518655.0  0.0093  0.0114  0.0301  0.0179  0.2413  0.0878  0.0350   
          518685.0  0.0083  0.0111  0.0282  0.0162  0.2115  0.0768  0.0320   
          518715.0  0.0081  0.0104  0.0270  0.0148  0.2052  0.0730  0.0318   

band                     9  
y         x                 
5212725.0 501915.0  0.0009  
          501945.0  0.0009  
          501975.0  0.0009  
          502005.0  0.0010  
          502035.0  0.0008  
...                    ...  
5198025.0 518595.0  0.0009  
          518625.0  0.0009  
          518655.0  0.0008  
          518685.0  0.0009  
          518715.0  0.0010  

[275357 rows x 8 columns]

In [45]:
# Check the data mins and max
min_values = model_df.min()
max_values = model_df.max()

# Print min/max values
print(min_values)
print(max_values)

band
1    0.0002
2    0.0003
3    0.0021
4    0.0001
5    0.0001
6    0.0002
7    0.0002
9    0.0005
dtype: float32
band
1    0.6302
2    0.6953
3    0.7493
4    0.8170
5    0.8450
6    0.9424
7    0.9538
9    0.0016
dtype: float32


Now we're reading to fit the k-means clustering model. We can run the fit and prediction functions at the same time because we don't have target data.

In [78]:
# Initialize k-means model 
k_means = KMeans(n_clusters = 6)

# Fit model and predict
prediction = k_means.fit_predict(model_df.values)

# Add the predicted values back to the model dataframe
model_df['clusters'] = prediction
model_df

band                     1       2       3       4       5       6       7  \
y         x                                                                  
5212725.0 501915.0  0.0151  0.0146  0.0279  0.0156  0.1930  0.0681  0.0270   
          501945.0  0.0165  0.0159  0.0314  0.0162  0.2213  0.0787  0.0312   
          501975.0  0.0159  0.0158  0.0313  0.0163  0.2185  0.0803  0.0304   
          502005.0  0.0165  0.0158  0.0293  0.0158  0.2173  0.0740  0.0299   
          502035.0  0.0168  0.0157  0.0346  0.0211  0.2444  0.0989  0.0435   
...                    ...     ...     ...     ...     ...     ...     ...   
5198025.0 518595.0  0.0093  0.0123  0.0311  0.0175  0.2348  0.0838  0.0350   
          518625.0  0.0094  0.0122  0.0318  0.0184  0.2515  0.0904  0.0368   
          518655.0  0.0093  0.0114  0.0301  0.0179  0.2413  0.0878  0.0350   
          518685.0  0.0083  0.0111  0.0282  0.0162  0.2115  0.0768  0.0320   
          518715.0  0.0081  0.0104  0.0270  0.0148  0.2052  0.0730  0.0318   

band                     9  clusters  
y         x                           
5212725.0 501915.0  0.0009         2  
          501945.0  0.0009         2  
          501975.0  0.0009         2  
          502005.0  0.0010         2  
          502035.0  0.0008         2  
...                    ...       ...  
5198025.0 518595.0  0.0009         2  
          518625.0  0.0009         2  
          518655.0  0.0008         2  
          518685.0  0.0009         2  
          518715.0  0.0010         2  

[275357 rows x 9 columns]

## STEP 5: Plot

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-task"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Try It</div></div><div class="callout-body-container callout-body"><p>Create a plot that shows the k-means clusters next to an RGB image of
the area. You may need to brighten your RGB image by multiplying it by
10. The code for reshaping and plotting the clusters is provided for you
below, but you will have to create the RGB plot yourself!</p>
<p>So, what is <code>.sortby(['x', 'y'])</code> doing for us? Try the
code without it and find out.</p></div></div>

In [59]:
# Make data array with bands to use for rgb: red, green, and blue
rgb = reflectance_da.sel(band = [4, 3, 2])

In [60]:
# Plot rbg
(
    rgb.hvplot.rgb(y = 'y',
                   x = 'x',
                   bands = 'band',
                   data_aspect = 1,
                   xaxis = None,
                   yaxis = None)
)

:RGB   [x,y]   (R,G,B)

In [61]:
# Stretch values
rgb_uint8 = (rgb * 255).astype(np.uint8).where(rgb != np.nan)

# Look at values
rgb_uint8

<xarray.DataArray 'reflectance' (band: 3, y: 491, x: 561)> Size: 3MB
array([[[ 3.,  4.,  4., ..., 35., 34., 31.],
        [ 3.,  4.,  4., ..., 33., 32., 27.],
        [ 4.,  4.,  4., ..., 30., 29., 28.],
        ...,
        [16., 25., 12., ...,  4.,  4.,  4.],
        [14., 24., 14., ...,  4.,  4.,  4.],
        [ 9., 11.,  7., ...,  4.,  4.,  3.]],

       [[ 7.,  8.,  7., ..., 25., 26., 23.],
        [ 7.,  8.,  8., ..., 26., 25., 21.],
        [ 7.,  8.,  8., ..., 24., 24., 20.],
        ...,
        [18., 23., 16., ...,  7.,  7.,  8.],
        [16., 22., 15., ...,  8.,  8.,  8.],
        [12., 13., 11., ...,  7.,  7.,  6.]],

       [[ 3.,  4.,  4., ..., 16., 17., 16.],
        [ 3.,  4.,  4., ..., 17., 18., 15.],
        [ 3.,  4.,  4., ..., 18., 17., 14.],
        ...,
        [10., 16.,  9., ...,  2.,  2.,  3.],
        [ 9., 15.,  9., ...,  3.,  3.,  3.],
        [ 6.,  6.,  5., ...,  2.,  2.,  2.]]],
      shape=(3, 491, 561), dtype=float32)
Coordinates:
  * band         (band) int64 24B 4 3 2
  * y            (y) float64 4kB 5.213e+06 5.213e+06 ... 5.198e+06 5.198e+06
  * x            (x) float64 4kB 5.019e+05 5.019e+05 ... 5.187e+05 5.187e+05
    spatial_ref  int64 8B 0

In [62]:
# Plot rbg from 0-255
(
    rgb_uint8.hvplot.rgb(y = 'y',
                   x = 'x',
                   bands = 'band',
                   data_aspect = 1,
                   xaxis = None,
                   yaxis = None)
)

:RGB   [x,y]   (R,G,B)

In [63]:
# Enhance brightness
rgb_uint8_bright = rgb_uint8 * 10

# Look at values
rgb_uint8_bright

<xarray.DataArray 'reflectance' (band: 3, y: 491, x: 561)> Size: 3MB
array([[[ 30.,  40.,  40., ..., 350., 340., 310.],
        [ 30.,  40.,  40., ..., 330., 320., 270.],
        [ 40.,  40.,  40., ..., 300., 290., 280.],
        ...,
        [160., 250., 120., ...,  40.,  40.,  40.],
        [140., 240., 140., ...,  40.,  40.,  40.],
        [ 90., 110.,  70., ...,  40.,  40.,  30.]],

       [[ 70.,  80.,  70., ..., 250., 260., 230.],
        [ 70.,  80.,  80., ..., 260., 250., 210.],
        [ 70.,  80.,  80., ..., 240., 240., 200.],
        ...,
        [180., 230., 160., ...,  70.,  70.,  80.],
        [160., 220., 150., ...,  80.,  80.,  80.],
        [120., 130., 110., ...,  70.,  70.,  60.]],

       [[ 30.,  40.,  40., ..., 160., 170., 160.],
        [ 30.,  40.,  40., ..., 170., 180., 150.],
        [ 30.,  40.,  40., ..., 180., 170., 140.],
        ...,
        [100., 160.,  90., ...,  20.,  20.,  30.],
        [ 90., 150.,  90., ...,  30.,  30.,  30.],
        [ 60.,  60.,  50., ...,  20.,  20.,  20.]]],
      shape=(3, 491, 561), dtype=float32)
Coordinates:
  * band         (band) int64 24B 4 3 2
  * y            (y) float64 4kB 5.213e+06 5.213e+06 ... 5.198e+06 5.198e+06
  * x            (x) float64 4kB 5.019e+05 5.019e+05 ... 5.187e+05 5.187e+05
    spatial_ref  int64 8B 0

In [64]:
# Plot brighter rgb
(
    rgb_uint8_bright.hvplot.rgb(y = 'y',
                   x = 'x',
                   bands = 'band',
                   data_aspect = 1,
                   xaxis = None,
                   yaxis = None)
)

:RGB   [x,y]   (R,G,B)

In [65]:
# Cap saturation
rgb_sat = rgb_uint8_bright.where(rgb_uint8_bright < 255, 255)

In [66]:
# Replot saturated aspect
(
    rgb_sat.hvplot.rgb(y = 'y',
                   x = 'x',
                   bands = 'band',
                   data_aspect = 1,
                   xaxis = None,
                   yaxis = None)
)

:RGB   [x,y]   (R,G,B)

In [79]:
# Plot the clusters from kmeans
(
    model_df.clusters.to_xarray().hvplot(
        x = 'x',
        y = 'y',
        data_aspect = 1,
        xaxis = None,
        yaxis = None)
)

:Image   [x,y]   (clusters)

In [80]:
# Plot the clusters from kmeans, deal with sorting
(
    model_df.clusters.to_xarray().sortby(['x', 'y']).hvplot(
        x = 'x',
        y = 'y',
        data_aspect = 1,
        xaxis = None,
        yaxis = None)
)

:Image   [x,y]   (clusters)

In [81]:
### plot the k-means clusters
(
     rgb_sat.hvplot.rgb(y = 'y',
                   x = 'x',
                   bands = 'band',
                   data_aspect = 1,
                   xaxis = None,
                   yaxis = None,
                   title = 'True Color Reflectance Composite (RGB)')
    + 
    model_df.clusters.to_xarray().sortby(['x', 'y']).hvplot(
        cmap="Colorblind", aspect='equal', title = 'Spectral Reflectance Clusters (K-Means)', data_aspect = 1) 
)

:Layout
   .RGB.I   :RGB   [x,y]   (R,G,B)
   .Image.I :Image   [x,y]   (clusters)

<link rel="stylesheet" type="text/css" href="./assets/styles.css"><div class="callout callout-style-default callout-titled callout-respond"><div class="callout-header"><div class="callout-icon-container"><i class="callout-icon"></i></div><div class="callout-title-container flex-fill">Reflect and Respond</div></div><div class="callout-body-container callout-body"><p>Don’t forget to interpret your plot!</p></div></div>

### **K-Means Land Cover Classification in Missippi Delta Watershed in Summer 2024**

Currently, New Orleans is one of the cities in the U.S. most vulnerable to impacts from climate change. This is in part due to the normal deltaic processes, such as subsidence, associated with being built on a river delta. New Orleans relies on engineering, through pumps and levees, to keep the city above water. Deltas rely on natural deposits of sediment to maintain their elevation. Due to these flooding interventions, the city is sinking. New Orleans experiences rapid land loss at an incredible rate of wetland loss the size of a football field every 100 minutes (Restore the Mississippi Delta, n.d.). This process is accelerated by climate change impacts such as increasing storm intensity (including hurricanes), faster sea-level rise, and other factors. Coastal and deltaic areas are important economic hubs as ports support the region and the nation. Ports have historically been important for economic growth and commerce; New Orleans is no exception (Day et al., 2021). The area was historically a significant wetland habitat, which has also been lost and degraded significantly due to development, land use, and the interruption of natural river hydrologic processes.

​This analysis used unsupervised machine learning, K-means, to look at land cover classifications in the watershed on the Mississippi Delta (HUC12 - 080902030506). Five K-Means clusters were used for this analysis. This area has significant wetland and saltwater intrusions, so we would expect those to be clustered. We can see some clustering that may be showing differences as the reflectance data for salt and fresh water. The salt water intrusions might be visible here, , with perhaps yellow being fresh water and dark blue being seawater. We also see clustering of what maybe land, wetlands, agriculture, development, and perhaps active erosion areas. The pink might be wetlands scattered throughout. In the RGB imagery, the water might appear brown due to high levels of suspended sediments in the water. The watershed is on the Mississippi River Delta, so we would expect a high sediment load. These wetlands and the deltaic watershed are very important for ecological health, biodiversity, and supporting fishing economies. In future analysis, it would be interesting to compare a time series of k-means to see any land cover classification differences. 


<u>Data Citation</u>
Masek, J., Ju, J., Roger, J.-C., Skakun, S., Vermote, E., Claverie, M., Dungan, J., Yin, Z., Freitag, B., &amp; Justice, C. (2021). <i>HLS Operational Land Imager Surface Reflectance and TOA Brightness Daily Global 30m v2.0</i> [Data set]. NASA Land Processes Distributed Active Archive Center. https://doi.org/10.5067/HLS/HLSL30.002 Date Accessed: 2026-02-07

<u>Citations</u>

- Day, J. W., Jr., Boesch, D. F., Clairain, E. J., Kemp, G. P., Laska, S. B., Mitsch, W. J., Mashriqui, H., Reed, D. J., Shabman, L., Simenstad, C. A., Streever, B. J., Twilley, R. R., Watson, C. C., Wells, J. T., & Whigham, D. F. (2007). Restoration of the Mississippi Delta: Lessons from Hurricanes Katrina and Rita. Science, 315(5819), 1679–1684. https://doi.org/10.1126/science.1137030

- Day, J. W., Hunter, R., Kemp, G. P., Moerschbaecher, M., & Brantley, C. G. (2021). The “problem” of New Orleans and diminishing sustainability of Mississippi River management — future options. Water, 13(6), 813. https://doi.org/10.3390/w13060813

- Restore the Mississippi River Delta Coalition. (n.d). Land loss in the Mississippi River Delta. Retrieved February 6, 2026, from https://mississippiriverdelta.org/our-coastal-crisis/land-loss/

- U.S. Geological Survey. (2011, November 11). The Mississippi River Delta Basin. U.S. Department of the Interior. Retrieved February 11, 2026, from https://eros.usgs.gov/media-gallery/image-of-the-week/the-mississippi-river-delta-basin